In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import os
import base64
from multiprocessing.managers import BaseManager
import io
from matplotlib import animation
import folium
import folium.plugins
from IPython.core.display import display, HTML


In [ ]:
warnings.filterwarnings("ignore")

In [ ]:
terror_data = pd.read_excel(r"D:\GitHub\World_Terrorism_Analysis\gtd_data.xlsx")
terror_data1 = pd.read_csv(r"D:\GitHub\World_Terrorism_Analysis\gtd_data.csv",encoding="ISO-8859-1") 

terror_data1.rename(columns={'iyear':'Year','imonth':'Month','iday':'Day','country_txt':'Country', 'city':'City', 'latitude':'Latitude', 'longitude':'Longitude', 'attacktype1_txt':'AttackType', 'nkill':'Death', 'nwound':'Injured', 'gname':'Attacker','targtype1_txt':'TargetType','weaptype1_txt':'WeaponType', 'weapsubtype1_txt':'WeaponSubType', 'weapdetail':'WeaponDetail'},inplace=True)



<h1>Exploratory Data Analysis</h1>

In [ ]:
#terror_data.head()

terror_data1.head()

In [ ]:
terror_data.shape

In [ ]:
terror_data.describe()

In [ ]:
terror_data.isnull().sum()

<h2>Basic Analysis</h2>

In [ ]:
print("Known Count of Deaths in Terrorist Attacks:", terror_data["Death"].value_counts()[0], "\n")

print("Country With The Highest Terrorist Attacks:", terror_data["Country"].value_counts().index[0], "\n")

print("Most deaths in an attack:\n",terror_data.loc[terror_data['Death'].idxmax()], "\n")

In [ ]:
plt.subplots(figsize=(15,6))
sns.countplot(data=terror_data, x="Year", palette="mako")
plt.xticks(rotation=90)
plt.title('Terrorist Attacks Each Year')
plt.show()

In [ ]:
plt.subplots(figsize=(12,6))
sns.countplot(data=terror_data, x="Target Type", order=terror_data["Target Type"].value_counts().index, palette="rocket")
plt.xticks(rotation=90)
plt.title('Terrorist Attacks Each Target')
plt.show()

In [ ]:
plt.subplots(figsize=(8,6))
sns.countplot(data=terror_data, x="Attack Type", order=terror_data["Attack Type"].value_counts().index, palette="rocket")
plt.xticks(rotation=90)
plt.title('Terrorist Attacks Each Attack Type')
plt.show()

In [104]:
def color_point(x):
    if x>=30:
        color='red'
    elif ((x>0 and x<30)):
        color='blue'
    else:
        color='green'
    return color  
    
def point_size(x):
    if (x>30 and x<100):
        size=2
    elif (x>=100 and x<500):
        size=8
    elif x>=500:
        size=16
    else:
        size=0.5
    return size   

terror_turkey=terror_data1[terror_data1["Country"]=="Turkey"]
terror_turkey_fol=terror_turkey.copy()
terror_turkey_fol.dropna(subset=["Latitude","Longitude"],inplace=True)
location_tr=terror_turkey_fol[["Latitude","Longitude"]][:5000]
city_tr=terror_turkey_fol["City"][:5000]
Death_tr=terror_turkey_fol["Death"][:5000]
Injured_tr=terror_turkey_fol["Injured"][:5000]
target_tr=terror_turkey_fol["TargetType"][:5000]

map1 = folium.Map(location=[38.9637, 35.2433],tiles='CartoDB dark_matter',zoom_start=6)
for point in location_tr.index:
    folium.CircleMarker(list(location_tr.loc[point].values),popup='<b>City: </b>'+str(city_tr[point])+'<br><b>Killed: </b>'+str(Death_tr[point])+'<br><b>Injured: </b>'+str(Injured_tr[point])+'<br><b>Target: </b>'+str(target_tr[point]),radius=point_size(Death_tr[point]),color=color_point(Death_tr[point]),fill_color=color_point(Death_tr[point])).add_to(map1)

map1

In [ ]:
fig = plt.figure(figsize = (10,8))
def animate(Year):
    ax = plt.axes()
    ax.clear()
    ax.set_title('Terrorism In India '+'\n'+'Year:' +str(Year))
    m5 = BaseManager(projection='lcc',resolution='l',llcrnrlon=67,llcrnrlat=5,urcrnrlon=99,urcrnrlat=37,lat_0=28,lon_0=77)
    lat_gif=list(terror_turkey[terror_turkey['Year']==Year].Latitude)
    long_gif=list(terror_turkey[terror_turkey['Year']==Year].Longitude)
    x_gif,y_gif=m5(long_gif,lat_gif)
    m5.scatter(x_gif, y_gif,s=[Death for Death in zip(terror_turkey[terror_turkey['Year']==Year].Death,terror_turkey[terror_turkey['Year']==Year])],color = 'r')
    m5.drawcoastlines()
    m5.drawcountries()
    m5.fillcontinents(color='coral',lake_color='aqua', zorder = 1,alpha=0.4)
    m5.drawmapboundary(fill_color='aqua')
ani = animation.FuncAnimation(fig,animate,list(terror_turkey.Year.unique()), interval = 1500)    
ani.save('animation.gif', writer='imagemagick', fps=1)
plt.close(1)
filename = 'animation.gif'
video = io.open(filename, 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<img src="data:image/gif;base64,{0}" type="gif" />'''.format(encoded.decode('ascii')))